In [1]:
#import basic modules
import glob
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import scipy as sp
import peak_utils

We will now load in all models so we can check which parts are significant. Only an example subset is stored on the github repo. You can download this data from the github repo or as a .tar.gz file from the website under the datasets section.


In [5]:
allnames = glob.glob('/home/bill/panel-examples/aphA/unsmoothed/*.txt')

In [21]:
RNAP_files = glob.glob('/home/bill/test_sets/RNAP/test_ident_all_sigm*')

In [22]:
def find_RNAP(s):
    gene = s['gene']
    try:
        RNAP_sites = get_RNAP_sites(alldf_RNAP[alldf_RNAP['gene'] == gene])
    except:
        RNAP_sites = []
    is_RNAP = False
    start = s['start']
    end = s['end']
    for RNAP in RNAP_sites:
        if ((start - 2 < RNAP) and (end > RNAP + 5)) or ((start < RNAP + 29) and (end > RNAP + 21)):
            is_RNAP = True
    
    return is_RNAP


In [23]:
def strip_blanks(s):
    return s.strip(' ')

In [24]:
alldf_RNAP = pd.DataFrame()
for Rf in RNAP_files:
    indf = pd.io.parsers.read_csv(Rf,delimiter='[',header=None)
    alldf_RNAP = pd.concat([alldf_RNAP,indf])
alldf_RNAP.reset_index(inplace=True,drop=True)
alldf_RNAP = alldf_RNAP.rename(columns={0:'gene',1:'sites'})
alldf_RNAP['gene'] = alldf_RNAP['gene'].apply(strip_blanks)    
    

In [25]:
alldf_RNAP.to_csv((open('/home/bill/test_sets/RNAP/comb_RNAP_sigma.csv','w')))

In [26]:
def get_RNAP_sites(s):
    outsites = []
    for i,row in s.iterrows():
        q = row['sites'].strip(']')
        q2 = q.split()
        q3 = [int(x) for x in q2]
        outsites = outsites + q3
    return list(set(outsites))

In [34]:
possible_growths = ['fructose','42','acetate','LB','heat','Anaero','arabinose','xylara','fum1','0cAMP','SS','arabionse','metal','Fe','xanth2','M9','Tre','deoR','phoP']

In [35]:
def find_edges(em,start,end):
    newstart = np.nan
    newend=np.nan
    em_abs = np.abs(em)
    for s in range(start,end+15):
        if em_abs[s] > thresh:
            newstart = s
            break
    for s in range(end+14,end-1,-1):
        if em_abs[s] > thresh:
            newend = s
            break
        elif s == end:
            newend = s
    return newstart, newend

In [36]:
def select_region(temp_significant,gene,growth):
    #initialize the variable 'ongoing'. this shows whether or not the current base is part of a binding site
    #or if its starting a new one.
    outdf = pd.DataFrame(columns=['gene','growth','feat_num','start','end','type'])
    ongoing = 0
    TF_type = 'None'
    num_feat = 0
    counter = 0
    length_info = len(temp_significant)
    #loop through only 145 base pairs (we don't go to 160 becuase the regions are 15 base pairs long.)
    for i in range(0,length_info-windowsize):
        
        #if we are not currently part of a binding site then we do this...
        if not ongoing:
            #if we have a new significant base pair we will start to log a new binding site.
            if (temp_significant[i-1] == 0 or temp_significant[i-1] == -1 or i == 0) and temp_significant[i] == 1:
                start = i
                ongoing = 1
                #we checked whether temp_signficant was '1' which means the effect of mutation on expression
                #is positive. This would indicate that the transcription factor type is 'repressor' 
                TF_type = 'rep'
            elif (temp_significant[i-1] == 0 or temp_significant[i-1] == 1 or i == 0) and temp_significant[i] == -1:
                start = i
                ongoing = 1
                #we checked whether temp_signficant was '-1' which means the effect of mutation on expression
                #is negative. This would indicate that the transcription factor type is 'activator' 
                TF_type = 'act'
        elif ongoing:                
            #if we are currently within an ongoing binding site we need to see whether or not the binding site
            #has ended at the current base. To do that we first check if the new base is not significant.
            future_sum = temp_significant[i:i+4].sum()
            if (temp_significant[i] == 0):
                #next, if there is only a 1-4 base pair break in which bases are above threshold, the whole
                #thing is probably still part of one binding site. So we check whether or not the next 4
                #base pairs are above threshold, if they are not we declare the binding site ended.
                #if the binding site is an activator, and none of the next four bases are also activator like
                #we end the binding site (if instead they are repressor like, in other words if
                #significant is > 0, then we can still assume the binding site has ended)
                if future_sum > -.5 and (TF_type == 'act'):
                    end = i
                    ongoing = 0
                    
                    #now that the current binding site has ended we will update the list of binding sites.
                    outdf.loc[counter,['gene','growth','feat_num','start','end','type']] = [gene,growth,num_feat,start,end,TF_type]
                    num_feat = num_feat + 1
                    TF_type = 'None'
                    counter = counter + 1
                #now do the same in the case that the current binding site is a repressor.
                elif future_sum < .5 and (TF_type == 'rep'):
                    end = i
                    ongoing = 0
                    outdf.loc[counter,['gene','growth','feat_num','start','end','type']] = [gene,growth,num_feat,start,end,TF_type]
                    num_feat = num_feat + 1
                    TF_type = 'None'
                    counter = counter + 1
                else:
                    pass
            elif (temp_significant[i-1] == 1 and temp_significant[i] == -1 and future_sum < .5):
                end = i
                outdf.loc[counter,['gene','growth','feat_num','start','end','type']] = [gene,growth,num_feat,start,end,TF_type]
                start = i
                num_feat = num_feat + 1
                TF_type = 'act'
                counter = counter + 1
            elif (temp_significant[i-1] == -1 and temp_significant[i] == 1 and future_sum > -.5):
                end = i
                outdf.loc[counter,['gene','growth','feat_num','start','end','type']] = [gene,growth,num_feat,start,end,TF_type]
                start = i
                num_feat = num_feat + 1
                TF_type = 'rep'
                counter = counter + 1
    if ongoing:
        if TF_type == 'rep':
            end = i
            ongoing = 0
            outdf.loc[counter,['gene','growth','feat_num','start','end','type']] = [gene,growth,num_feat,start,end,TF_type]
            num_feat = num_feat + 1
            TF_type = 'None'
            counter = counter + 1
        elif TF_type == 'act':
            end = i
            ongoing = 0
            #now that the current binding site has ended we will update the list of binding sites.
            outdf.loc[counter,['gene','growth','feat_num','start','end','type']] = [gene,growth,num_feat,start,end,TF_type]
            num_feat = num_feat + 1
            TF_type = 'None'
            counter = counter + 1
            #now do the same in the case that the current binding site is a repressor.
        
    return outdf
                

In [37]:
threshs = [0.00025]

In [8]:
def merge_growths(df,length_info=160):
    allgenes = list(set(df['gene']))
    processed_df = pd.DataFrame(columns=['gene','feat_num','start','end','type'])
    counter = 0
    for gene in allgenes:
        tempdf = df.loc[df['gene'] == gene]
        allgrowths = list(set(tempdf['growth']))
        all_acts_df = tempdf.loc[tempdf['type']=='act']
        all_rep_df = tempdf.loc[tempdf['type']=='rep']
        act_array = np.zeros(length_info)
        rep_array = np.zeros(length_info)
        
        for i,row in all_acts_df.iterrows():
            act_array[int(row['start']):int(row['end'])] = 1
        for i,row in all_rep_df.iterrows():
            rep_array[int(row['start']):int(row['end'])] = 1

        outdf_temp_rep = select_region(rep_array,gene,'arabinose')

        outdf_temp_act = select_region(act_array,gene,'arabinose')

        if len(all_acts_df.index) != 0:
            for i,row in outdf_temp_act.iterrows():
                start = row['start']
                end = row['end']
                processed_df.loc[counter,['gene','feat_num','start','end','type']] = [row['gene'],row['feat_num'],start,end,'act']
                counter = counter + 1
        if len(all_rep_df.index) != 0:
            for i,row in outdf_temp_rep.iterrows():
                start = row['start']
                end = row['end']
                processed_df.loc[counter,['gene','feat_num','start','end','type']] = [row['gene'],row['feat_num'],start,end,'rep']
                counter = counter + 1
            
    return processed_df
        

In [25]:
#we set an averaging size of 15, as this is a typical size for a binding site.
windowsize = 15
def do_sum2(s,length_info=160):
    '''this function does a summation 15 base pairs'''
    outarr = np.zeros(length_info - windowsize)
    for i in range(length_info - windowsize):
        outarr[i] = s[i:(i+windowsize)].sum()
    return outarr


#we define some column names. The only purpose of that these are the columns that are used in 
#the any energy matrices.
val_cols = ['val_A','val_C','val_G','val_T']

for thresh in threshs:
    counter = 0
    outdf = pd.DataFrame(columns=['gene','growth','feat_num','start','end','type'])    
    for name in allnames:
        try:
            noleader = name.split('/')[-1]

            for x in possible_growths:
                if x in noleader and '500cAMP' not in x and noleader.split('dataset')[0] != '':
                    growth = x
                    if growth == 'acetate' or growth == '42' or growth == 'fructose' or growth == '_comb':
                        gene = noleader.split('dataset')[0]
                    else:
                        gene = noleader.split(growth)[0]
            #load in information footprint
            df = pd.io.parsers.read_csv(name,delim_whitespace=True)
            length_info = len(df['info'])
            em = np.abs(np.array(list(df['info'])))
  
            #invert information values.
            em_noabs = em_noabs*-1

            #split the information footprint into two groups of repressor like and activator like bases.
            pos_mat = np.zeros(length_info)
            neg_mat = np.zeros(length_info)
            for q in range(len(em_noabs)):
                if em_noabs[q] > 0:
                    pos_mat[q] = np.abs(em_noabs[q])
                else:
                    neg_mat[q] = np.abs(em_noabs[q])

            #sum over 15 base pair windows
            summedarr2 = do_sum2(pos_mat)
            summedarr2_neg = do_sum2(neg_mat)

            #initialize array where we will store whether or not the outcome beats threshold.
            is_significant = np.zeros(length_info-windowsize)
            is_significant_neg = np.zeros(length_info-windowsize)
            for i in range(length_info-windowsize):
                is_significant[i] = summedarr2[i] > thresh*windowsize
            
                
                is_significant_neg[i] = summedarr2_neg[i] > thresh*windowsize
                is_significant_neg[i] = is_significant_neg[i]*-1
    
            outdf_temp = select_region(is_significant,gene,growth)
            outdf_temp2 = select_region(is_significant_neg,gene,growth)
            for i,row in outdf_temp.iterrows():
                start = row['start']
                end = row['end']
                newstart,newend = find_edges(pos_mat,start,end)
                outdf.loc[counter,['gene','growth','feat_num','start','end','type']] = [row['gene'],growth,row['feat_num'],newstart,newend,row['type']]
                counter = counter + 1
            for i,row in outdf_temp2.iterrows():
                start = row['start']
                end = row['end']
                newstart,newend = find_edges(neg_mat,start,end)
                outdf.loc[counter,['gene','growth','feat_num','start','end','type']] = [row['gene'],growth,row['feat_num'],newstart,newend,row['type']]
                counter = counter + 1
        except Exception as e:
            print(e)
            
    outdf['RNAP'] = outdf.apply(find_RNAP,axis=1)
    outdf.to_csv('/media/bill/New_Volume/software/all_features_auto20_for_check_split_' + str(thresh) + '.csv')
    z = merge_growths(outdf)
    z['RNAP'] = z.apply(find_RNAP,axis=1)
    z.to_csv('/media/bill/New_Volume/software/all_features_auto_merged_20_scaled_for_RNAP_check_' + str(thresh) + '.csv')

       gene  growth feat_num start  end type   RNAP
74     adiY      SS        0     9   29  act  False
75     adiY      SS        1    22   50  act  False
76     adiY      SS        2    90  111  act  False
77     adiY      SS        3   110  135  act  False
80     adiY      SS        0     4   16  act  False
...     ...     ...      ...   ...  ...  ...    ...
10877  adiY      SS        2   110  135  act  False
11889  adiY  Anaero        0    12   41  act  False
11890  adiY  Anaero        1    41   65  act  False
11891  adiY  Anaero        2    58   84  act  False
11892  adiY  Anaero        3    95  135  act  False

[66 rows x 7 columns]
       gene  growth feat_num start  end type   RNAP
70     adiY      SS        0    74   89  rep  False
71     adiY      SS        1    85   96  rep  False
72     adiY      SS        2   126  138  rep  False
73     adiY      SS        3   148  156  rep  False
78     adiY      SS        0    64   78  rep  False
...     ...     ...      ...   ...  ...  

[1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 0. 0.]
[1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 0. 0.]
htrB
   gene     growth 

0  ompR  arabinose        0     0  144  rep
       gene  growth feat_num start  end type   RNAP
934    mscK   0cAMP        0    10   32  act  False
935    mscK   0cAMP        1    57   74  act  False
936    mscK   0cAMP        2    92  104  act   True
937    mscK   0cAMP        3   101  115  act   True
938    mscK   0cAMP        4   115  128  act  False
...     ...     ...      ...   ...  ...  ...    ...
12166  mscK    fum1        0     1   13  act  False
12167  mscK    fum1        1    13   86  act   True
12168  mscK    fum1        2    81  157  act   True
13289  mscK  Anaero        0    27   41  act  False
13290  mscK  Anaero        1    50   65  act  False

[61 rows x 7 columns]
       gene  growth feat_num start  end type   RNAP
931    mscK   0cAMP        0     3   30  rep  False
932    mscK   0cAMP        1    43   66  rep  False
933    mscK   0cAMP        2    80   91  rep  False
3814   mscK    heat        0    55   65  rep  False
4728   mscK     Tre        0    19   48  rep  Fal

0  arcB  arabinose        0     2  144  rep
       gene   growth feat_num start  end type   RNAP
996    zapB   xylara        0     2   35  act  False
997    zapB   xylara        1    35   49  act  False
998    zapB   xylara        2    63  118  act   True
999    zapB   xylara        3   118  127  act  False
1000   zapB   xylara        4   140  158  act  False
...     ...      ...      ...   ...  ...  ...    ...
12897  zapB   xanth2        4   113  127  act  False
12898  zapB   xanth2        5   140  158  act  False
13319  zapB  acetate        0    15   63  act  False
13320  zapB  acetate        1    56  128  act   True
13321  zapB  acetate        2   140  158  act  False

[101 rows x 7 columns]
       gene   growth feat_num start  end type   RNAP
994    zapB   xylara        0    51  112  rep   True
995    zapB   xylara        1   124  148  rep  False
1532   zapB  acetate        0    32   42  rep  False
1533   zapB  acetate        1    42  113  rep   True
1534   zapB  acetate        2  

[0. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 0. 0. 0.]
[1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 0. 0. 0.]
yehS
   gene     growth 

...

      gene  growth feat_num start  end type   RNAP
61    ycbZ   metal        0    78   92  act   True
62    ycbZ   metal        1   101  122  act   True
336   ycbZ     Tre        0    78   92  act   True
337   ycbZ     Tre        1   101  123  act   True
392   ycbZ     Tre        0    78   92  act   True
393   ycbZ     Tre        1   101  123  act   True
515   ycbZ    heat        0    78   92  act   True
516   ycbZ    heat        1   101  123  act   True
609   ycbZ  Anaero        0    77  112  act   True
1246  ycbZ      LB        0    76  112  act   True
1268  ycbZ   metal        0    78   92  act   True
1269  ycbZ   metal        1   101  123  act   True
1732  ycbZ  xylara        0    77  101  act   True
1733  ycbZ  xylara        1    92  123  act   True
1734  ycbZ    phoP        0    90   99  act   True
1934  ycbZ    phoP        0    78   92  act   True
1935  ycbZ    phoP        1    92  111  act   True
1940  ycbZ  xanth2        0    77  101  act   True
1941  ycbZ  xanth2        1    

   gene     growth feat_num start  end type
0  yehT  arabinose        0    69   82  rep
1  yehT  arabinose        1    96  138  rep
hi
   gene     growth feat_num start  end type
0  yehT  arabinose        0    69   92  rep
1  yehT  arabinose        1   103  111  rep
      gene  growth feat_num start  end type   RNAP
329   ilvC      M9        0    82  104  act   True
406   ilvC      Fe        0    40   87  act   True
407   ilvC      Fe        1    98  119  act   True
442   ilvC  xylara        0    59   76  act  False
443   ilvC  xylara        1    69   87  act   True
444   ilvC  xylara        2    98  117  act   True
699   ilvC  xylara        0    59   74  act  False
700   ilvC  xylara        1    69   87  act   True
701   ilvC  xylara        2    98  117  act   True
722   ilvC  xanth2        0    51   63  act  False
723   ilvC  xanth2        1    73   87  act   True
724   ilvC  xanth2        2    98  117  act   True
831   ilvC      M9        0    82  104  act   True
942   ilvC  xanth2 

      gene  growth feat_num start  end type   RNAP
351   yedK      M9        0   101  111  act   True
352   yedK      M9        1   126  140  act   True
374   yedK    deoR        0   116  132  act   True
511   yedK    deoR        0   125  138  act   True
590   yedK      Fe        0   112  142  act   True
625   yedK  xylara        0   119  142  act   True
687   yedK   metal        0   101  116  act   True
688   yedK   metal        1   114  139  act   True
706   yedK    deoR        0   116  132  act   True
1456  yedK   metal        0   101  116  act   True
1457  yedK   metal        1   114  139  act   True
1829  yedK    heat        0   101  116  act   True
1830  yedK    heat        1   115  140  act   True
2128  yedK      Fe        0   112  142  act   True
2270  yedK    deoR        0   125  138  act   True
2414  yedK  Anaero        0   122  142  act   True
2421  yedK      M9        0   104  111  act   True
2422  yedK      M9        1   126  140  act   True
2468  yedK     Tre        0   1

 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 0. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1. 1.
 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 1. 1. 1. 1. 0. 0. 0. 0. 0. 0.]
yehU
   gene     growth feat_num start  end type
0  yehU  arabinose        0    32  122  rep
hi
   gene     growth feat_num start end type
0  yehU  arabinose        0    60  83  rep
      gene   growth feat_num start  end type   RNAP
42    thiM      Tre        0    73   86  act   True
43    thiM      Tre        1   102  117  act   True
479   thiM     fum1        0    69   95  act   True
480   thiM     fum1        1    90  117  act   True
621   thiM       LB 

   gene     growth feat_num start  end type
0  yjjJ  arabinose        0    61  138  rep
hi
   gene     growth feat_num start  end type
0  yjjJ  arabinose        0    91  133  rep
      gene growth feat_num start  end type   RNAP
1535  ybjX     LB        0    25   43  act  False
1536  ybjX     LB        1    98  107  act  False
Empty DataFrame
Columns: [gene, growth, feat_num, start, end, type, RNAP]
Index: []
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 1. 1. 1. 1. 1. 1. 1. 1